La distribución del campo electrico
$$
\vec E = \frac{1}{4\pi \epsilon_0}\int_\Omega \frac{\vec r - \vec r'}{|\vec r - \vec r'|^3} dq
$$
en donde el diferencial de carga tiene distintas formas dependiendo de las coordenadas y distribución
$$
dq = \rho(\vec r') d^3r'
$$

In [1]:
import numpy as np
import scipy as sp
from scipy.integrate import quad

import matplotlib.pyplot as plt
import sympy as smp
import plotly.graph_objects as go
from IPython.display import HTML

# Primer Grafico con vectores un dipolo

In [107]:
# definiendo variables
t = smp.symbols('t',positive=True)
x,y,z = smp.symbols('x y z')
r = smp.Matrix([x,y,z])
r

Matrix([
[x],
[y],
[z]])

In [113]:


# distribución

rparticulas_numpy = np.array( [
    [1,0,0], [-1,0,0]
    ])
charge = [1,-1]

rp1 = smp.Matrix( rparticulas_numpy[0] )
rp2 = smp.Matrix( rparticulas_numpy[1] )
rparticulas = [rp1,rp2]

E = smp.Matrix([0,0,0])
for i,rp in enumerate(rparticulas):
    dist = r - rp

    E += charge[i] * dist / dist.norm()**3

E


Matrix([
[(-x - 1)/(Abs(y)**2 + Abs(z)**2 + Abs(x + 1)**2)**(3/2) + (x - 1)/(Abs(y)**2 + Abs(z)**2 + Abs(x - 1)**2)**(3/2)],
[            -y/(Abs(y)**2 + Abs(z)**2 + Abs(x + 1)**2)**(3/2) + y/(Abs(y)**2 + Abs(z)**2 + Abs(x - 1)**2)**(3/2)],
[            -z/(Abs(y)**2 + Abs(z)**2 + Abs(x + 1)**2)**(3/2) + z/(Abs(y)**2 + Abs(z)**2 + Abs(x - 1)**2)**(3/2)]])

In [114]:
def E_func(xx,yy,zz):
    return np.array([
        smp.lambdify([x,y,z],E[0])(xx,yy,zz),
        smp.lambdify([x,y,z],E[1])(xx,yy,zz),
        smp.lambdify([x,y,z],E[2])(xx,yy,zz)
    ])
    

In [115]:
# meshgrid
N = 18
xv = np.linspace(-3,3,N)
yv = np.linspace(-3,3,N)
zv = np.linspace(0,2*np.pi,N)
X,Y,Z = np.meshgrid(xv,yv,zv)


E_field = np.vectorize(E_func, signature='(),(),()->(n)')(X,Y,Z)

In [116]:
Ex = E_field[:,:,:,0]
Ey = E_field[:,:,:,1]
Ez = E_field[:,:,:,2]

data = go.Cone(
    x=X.ravel(), y=Y.ravel(), z=Z.ravel(),
    u = Ex.ravel(), v=Ey.ravel(), w=Ez.ravel(),
            colorscale='viridis', sizemode='scaled', sizeref=1)
layout = go.Layout(title=r'Campo Electrico 2 particulas',
    scene=dict(
        xaxis_title=r'x',
        yaxis_title=r'y',
        zaxis_title=r'z',
        camera_eye={'x':1.2,'y':1.2,'z':1.2}
    ))

fig = go.Figure(data=data, layout=layout)
fig.add_scatter3d(
    x=rparticulas_numpy[:,0], y=rparticulas_numpy[:,1], z=rparticulas_numpy[:,2]
    )

#HTML(fig.to_html(default_width=1000, default_height=1000))
fig.show()

# Grafico de Vectores para distribucion continua
Un loop cargado, con radio $R=1$ y con posición parametrizada por $t \in [0, 2\pi]$ 
$$
\vec r' = \{\cos 4t, \sin 4t, t\}
$$



In [53]:
# definiendo variables
t = smp.symbols('t',positive=True)
x,y,z = smp.symbols('x y z')
r = smp.Matrix([x,y,z])

# distribución
rp = smp.Matrix([smp.cos(4*t), smp.sin(4*t),t])

dist = r - rp

usamos $dq = \lambda dt$ en donde 
$$\lambda = \frac{1}{\int |d\vec r'/dt| dt}$$

In [54]:
drp_dt = smp.diff(rp,t).norm().simplify()
drp_dt # la norma

lambd = 1/  smp.integrate(drp_dt, (t,0,2*smp.pi))
lambd

sqrt(17)/(34*pi)

el integranod será ahora
$$
\frac{\vec r - \vec r'}{|\vec r - \vec r'|^3} \lambda |\frac{d\vec r}{dt}| 
$$

In [55]:
integrand = lambd * dist/dist.norm()**3 * drp_dt
integrand 

Matrix([
[(x - cos(4*t))/(2*pi*(Abs(t - z)**2 + Abs(x - cos(4*t))**2 + Abs(y - sin(4*t))**2)**(3/2))],
[(y - sin(4*t))/(2*pi*(Abs(t - z)**2 + Abs(x - cos(4*t))**2 + Abs(y - sin(4*t))**2)**(3/2))],
[      (-t + z)/(2*pi*(Abs(t - z)**2 + Abs(x - cos(4*t))**2 + Abs(y - sin(4*t))**2)**(3/2))]])

calculamos los componentes diferenciales del campo electrico de manera simbolica y lo evaluamos como una función

In [56]:
dExdt = smp.lambdify([t,x,y,z], integrand[0])
dEydt = smp.lambdify([t,x,y,z], integrand[1])
dEzdt = smp.lambdify([t,x,y,z], integrand[2])

def E(x,y,z):
    return np.array([
        quad(dExdt,0,2*np.pi, args=(x,y,z))[0],
        quad(dEydt,0,2*np.pi, args=(x,y,z))[0],
        quad(dEzdt,0,2*np.pi, args=(x,y,z))[0],

    ])

Crear un meshgrid

In [57]:
N = 18
x = np.linspace(-3,3,N)
y = np.linspace(-3,3,N)
z = np.linspace(0,2*np.pi,N)
X,Y,Z = np.meshgrid(x,y,z)
X.shape

(18, 18, 18)

usando vectorización es posible obtener resultados más rapidos

In [58]:
# esta parte es altamente paralelizable
E_field = np.vectorize(E, signature='(),(),()->(n)')(X,Y,Z)
Ex = E_field[:,:,:,0]
Ey = E_field[:,:,:,1]
Ez = E_field[:,:,:,2]


graficar en 3D

In [ ]:
# corre esta celda si no sabes que hace la siguiente función
Ex.ravel?

In [48]:
# parametrizamos la figura como puntos scatter
tt = np.linspace(0,2*np.pi,200)
lx,ly,lz = np.cos(4*tt),np.sin(4*tt), tt

In [50]:
data = go.Cone(x=X.ravel(), y=Y.ravel(), z=Z.ravel(),
            u = Ex.ravel(), v=Ey.ravel(), w=Ez.ravel(),
            colorscale='viridis', sizemode='scaled', sizeref=1)
layout = go.Layout(title=r'Campo Electrico de Resorte',
    scene=dict(
        xaxis_title=r'x',
        yaxis_title=r'y',
        zaxis_title=r'z',
        camera_eye={'x':1.2,'y':1.2,'z':1.2}
    ))

fig = go.Figure(data=data, layout=layout)
fig.add_scatter3d(x=lx, y=ly, z=lz, mode='lines', line=dict(color='green', width=10))

#HTML(fig.to_html(default_width=1000, default_height=1000))
fig.show()

# Una sola función para graficar

In [67]:
t = smp.symbols('t',positive=True)
    
def calculateE(X,Y,Z, rp, drp_dt, rho, ti, tf, titulo=r"Campo E"):
    """ calcula el campo electrico para distribución lineal
    rp = smp.Matrix([rx(t), ry(t), rz(t)])
    drp_dt = smp.diff(rp,t).norm().simplify()
    rho = 1/  smp.integrate(drp_dt, (t,ti,tf))
    """
    x,y,z = smp.symbols('x y z')
    r = smp.Matrix([x,y,z])
    dist = r - rp
    
    integrand = rho * dist/dist.norm()**3 * drp_dt
    dExdt = smp.lambdify([t,x,y,z], integrand[0])
    dEydt = smp.lambdify([t,x,y,z], integrand[1])
    dEzdt = smp.lambdify([t,x,y,z], integrand[2])

    def E(x,y,z):
        return np.array([
            quad(dExdt, ti,tf, args=(x,y,z))[0],
            quad(dEydt, ti,tf, args=(x,y,z))[0],
            quad(dEzdt, ti,tf, args=(x,y,z))[0],

        ])
    
    E_field = np.vectorize(E, signature='(),(),()->(n)')(X,Y,Z)
    Ex = E_field[:,:,:,0]
    Ey = E_field[:,:,:,1]
    Ez = E_field[:,:,:,2]
    data = go.Cone(x=X.ravel(), y=Y.ravel(), z=Z.ravel(),
            u = Ex.ravel(), v=Ey.ravel(), w=Ez.ravel(),
            colorscale='viridis', sizemode='scaled', sizeref=1)
    layout = go.Layout(title=titulo,
        scene=dict(
            xaxis_title=r'x',
            yaxis_title=r'y',
            zaxis_title=r'z',
            camera_eye={'x':1.2,'y':1.2,'z':1.2}
        ))

    fig = go.Figure(data=data, layout=layout)
    return fig



## Campo Electrico de una linea

In [66]:
# densidad de carga
ti,tf=-1,1
t = smp.symbols('t',positive=True)
rp = smp.Matrix([0, 0, t])
drp_dt = smp.diff(rp,t).norm().simplify()
rho = 1/smp.integrate(drp_dt, (t,ti,tf))

# vectores de posición r
N = 18
x = np.linspace(-1,1,N)
y = np.linspace(-1,1,N)
z = np.linspace(-2,2,N)
X,Y,Z = np.meshgrid(x,y,z)

fig = calculateE(X,Y,Z,rp, drp_dt, rho, ti, tf)

# parametrizamos la figura como puntos scatter
tt = np.linspace(ti,tf,100)
lx,ly,lz = 0*tt,0*tt, tt


fig.add_scatter3d(x=lx, y=ly, z=lz, mode='lines', line=dict(color='green', width=10))
fig.show()

## Campo Electrico superficie plana
Ocurre que el diferencial de carga puede ser expresado como
$$
dq = \sigma dx \, dy
$$

In [117]:
# densidad de carga
li,lf=-10,10
xp = smp.symbols('xp')
yp = smp.symbols('yp')

rp = smp.Matrix([xp, yp, 0])
drp_dt = smp.diff(rp,xp).cross( smp.diff(rp,yp) ).norm().simplify()
rho = 1/smp.integrate(drp_dt, (xp,li,lf), (yp,li,lf))
rho

1/400

In [119]:
from scipy.integrate import dblquad
# vectores de posición r
N = 10
x = np.linspace(-2,2,N)
y = np.linspace(-2,2,N)
z = np.linspace(-2,2,N)
X,Y,Z = np.meshgrid(x,y,z)

# Calculo del campo electrico
x,y,z = smp.symbols('x y z')
r = smp.Matrix([x,y,z])
dist = r - rp

integrand = rho * dist/dist.norm()**3 * drp_dt
dExdt = smp.lambdify([xp,yp,x,y,z], integrand[0])
dEydt = smp.lambdify([xp,yp,x,y,z], integrand[1])
dEzdt = smp.lambdify([xp,yp,x,y,z], integrand[2])

In [120]:

def E(x,y,z):
    return np.array([
        dblquad(dExdt, li,lf,li,lf, args=(x,y,z))[0],
        dblquad(dEydt, li,lf,li,lf, args=(x,y,z))[0],
        dblquad(dEzdt, li,lf,li,lf, args=(x,y,z))[0],

    ])


In [121]:

E_field = np.vectorize(E, signature='(),(),()->(n)')(X,Y,Z)
Ex = E_field[:,:,:,0]
Ey = E_field[:,:,:,1]
Ez = E_field[:,:,:,2]


In [122]:
titulo = "Campo E plano cargado"
data = go.Cone(x=X.ravel(), y=Y.ravel(), z=Z.ravel(),
        u = Ex.ravel(), v=Ey.ravel(), w=Ez.ravel(),
        colorscale='viridis', sizemode='scaled', sizeref=.6)
layout = go.Layout(title=titulo,
    scene=dict(
        xaxis_title=r'x',
        yaxis_title=r'y',
        zaxis_title=r'z',
        camera_eye={'x':1.2,'y':1.2,'z':1.2}
    ))

fig = go.Figure(data=data, layout=layout)

# parametrizamos la figura como puntos scatter
lx,ly,lz =np.linspace(li,lf,100),np.linspace(li,lf,100), np.zeros(100)
LX,LY = np.meshgrid(lx,ly)
LZ = np.zeros_like(LX) 


fig.add_surface(x=LX, y=LY, z=LZ)
fig.show()